In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install numpy  # установить эту версию нужно лишь для верного импорта BERTopic
import ast

In [ ]:
#%%capture
!pip install bertopic # https://github.com/MaartenGr/BERTopic
# https://colab.research.google.com/drive/1FieRA9fLdkQEGDIMYl0I3MCjSUKVF8C-?usp=sharing#scrollTo=edzNhZuZ6wTr

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.4/143.4 kB 1.8 MB/s eta 0:00:00
  Using cached hdbscan-0.8.33.tar.gz (5.2 MB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached umap-learn-0.5.3.tar.gz (88 kB)
  Preparing metadata (setup.py) ... done
  Using cached sentence-transformers-2.2.2.tar.gz (85 kB)
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 49.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 45.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 20.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 35.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 98.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 78.5 MB/s eta 0:00:00
  Created wheel for hdbscan: filen

In [ ]:
import glob
from bertopic import BERTopic
import re

In [ ]:
way = glob.glob('/content/drive/MyDrive/ВКонтакте/MARCH_2023_Обработанные посты_отдельно_BERTopic/*.txt')
author2doc = dict()
for w in way:
  w = w.replace('/content/drive/MyDrive/ВКонтакте/MARCH_2023_Обработанные посты_отдельно_BERTopic/', '')
  w = re.sub('\_POST\_[0-9]+\_PROCESSED\.txt', '', w)
  if w not in author2doc:
    author2doc[w] = []

In [ ]:
len(way)

10449

In [ ]:
# Путь к папке со всеми документами
docs = [] #сами документы и их ID
doc_ids = []

In [ ]:
way = glob.glob('/content/drive/MyDrive/ВКонтакте/MARCH_2023_Обработанные посты_отдельно_BERTopic/*')
for pair in author2doc:
  for w in way:
    check = w.replace('/content/drive/MyDrive/ВКонтакте/MARCH_2023_Обработанные посты_отдельно_BERTopic/', '')
    check = re.sub('\_POST\_[0-9]+\_PROCESSED\.txt', '', check)
    if pair in check:
      if w not in doc_ids:
        author2doc[pair].append(w)
        doc_ids.append(w)
        lemmata = open(w, encoding='utf-8').read()
        lemmata = ast.literal_eval(lemmata)
        docs.append(lemmata)

In [ ]:
len(docs)

10449

In [ ]:
frame = []

count = 0

for i in author2doc:
  try:
    documents = []
    for path in author2doc[i]:
      lemmata = open(path, encoding = 'utf8').read()
      lemmata = ast.literal_eval(lemmata)
      for sent in lemmata:
        documents.append(sent)

    topic_model = BERTopic(language="multilingual", calculate_probabilities=True, verbose=True, top_n_words=10)  # min_topic_size для тех случаев, когда тем у автора больше 1000, а объём файла -- больше 10 мб.
    topics, probs = topic_model.fit_transform(documents)
    freq = topic_model.get_topic_info()
    print(freq)
    # -1 refers to all outliers and should typically be ignored. Next, let's take a look at the most frequent topic that was generated
    number = len(freq) - 1  # кол-во топиков = длина списка - 1 (выбросы)
    # number = 10  # 10 тем -- среднее количество тем у каждого пользователя
    n = [i, ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ']
    frame.append(n)
    topic = []
    for i in range(0, number):
      topic.append(i)
      for t in topic_model.get_topic(i):
        topic.append(t[0])
        if len(topic) == 11:  # если все 10 слов даны, а не 9 и меньше
          print(topic)
          frame.append(topic)
          # print(topic)
      topic = []
    count += 1
    print('The model has prcocessed '+str(count)+' author(s)!')
  except:
    n = [i, ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ', ' ']
    frame.append(n)
    print(i+' is too small!')
    count += 1
    print('The model has prcocessed '+str(count)+' author(s)!')

Batches:   0%|          | 0/6 [00:00<?, ?it/s]

2023-03-09 17:50:33,332 - BERTopic - Transformed documents to Embeddings
2023-03-09 17:50:42,236 - BERTopic - Reduced dimensionality
2023-03-09 17:50:42,258 - BERTopic - Clustered reduced embeddings


   Topic  Count                                 Name
0     -1     49            -1_друг_самка_время_замок
1      0     85      0_человек_хороший_первый_любить
2      1     23  1_фотограф_фотография_фото_общество
3      2     20           2_зверь_собака_гепард_день
4      3     12            3_ночь_хороший_день_белый
[0, 'человек', 'хороший', 'первый', 'любить', 'счастливый', 'писать', 'друг', 'день', 'книжка', 'слово']
[1, 'фотограф', 'фотография', 'фото', 'общество', 'фотографический', 'номинация', 'картинка', 'петербургский', 'сезон', 'плетенский']
[2, 'зверь', 'собака', 'гепард', 'день', 'свет', 'африка', 'котик', 'утренний', 'антилоп', 'три']
[3, 'ночь', 'хороший', 'день', 'белый', 'дождь', 'апельсин', 'погода', 'холодный', 'цвести', 'прощание']
The model has prcocessed 1 author(s)!


Batches:   0%|          | 0/52 [00:00<?, ?it/s]

2023-03-09 17:50:45,403 - BERTopic - Transformed documents to Embeddings
2023-03-09 17:50:54,438 - BERTopic - Reduced dimensionality
2023-03-09 17:50:54,629 - BERTopic - Clustered reduced embeddings


...

2023-03-09 18:54:34,368 - BERTopic - Transformed documents to Embeddings
2023-03-09 18:54:40,072 - BERTopic - Reduced dimensionality
2023-03-09 18:54:40,150 - BERTopic - Clustered reduced embeddings


    Topic  Count                                       Name
0      -1    314              -1_человек_делать_книга_закон
1       0    130                  0_два_носить_человек_заяц
2       1     92              1_ребенок_родитель_семья_член
3       2     84          2_автомобиль_водитель_курс_дорога
4       3     44           3_диалог_слышать_контакт_молчать
5       4     41   4_помощники_слово_наказывать_оправдывать
6       5     34      5_школа_скольжение_курс_преподаватель
7       6     30     6_участник_приз_участвовать_сертификат
8       7     26           7_библия_бог_приложение_название
9       8     26                  8_день_час_неделя_февраль
10      9     26    9_тревога_компульсивный_страдание_страх
11     10     17        10_репост_телеграмм_сообщение_отзыв
12     11     14                    11_зимний_зима_лёд_курс
13     12     12  12_знаменитость_раздражать_звезда_обычный
14     13     12          13_понимать_русский_крым_западный
15     14     12    14_мнение_часть_прог

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

2023-03-09 18:54:43,127 - BERTopic - Transformed documents to Embeddings
2023-03-09 18:54:47,362 - BERTopic - Reduced dimensionality
2023-03-09 18:54:47,391 - BERTopic - Clustered reduced embeddings


   Topic  Count                                 Name
0     -1     33    -1_кирпичный_волос_печь_программа
1      0     52             0_друг_печь_искать_пойти
2      1     30           1_концерт_новый_хип_альбом
3      2     13  2_бесплатный_выгодный_покупка_билет
[0, 'друг', 'печь', 'искать', 'пойти', 'спать', 'умение', 'барный', 'лето', 'вкус', 'летие']
[1, 'концерт', 'новый', 'хип', 'альбом', 'сольный', 'гость', 'хоп', 'группа', 'конец', 'лучший']
[2, 'бесплатный', 'выгодный', 'покупка', 'билет', 'платить', 'ссылка', 'карта', 'плат', 'переходить', 'абонентский']
The model has prcocessed 661 author(s)!


In [ ]:
# Save model
topic_model.save("PhD_Model_BERTopic_MARCH_2023")

In [ ]:
# Load model
topic_model = BERTopic.load('drive/MyDrive/Кандидатская диссертация/Корпус социальных медиа/ВКонтакте/МАРТ 2023/PhD_Model_BERTopic_MARCH_2023')

In [ ]:
topic_model

In [ ]:
import pandas as pd

In [ ]:
df_1 = pd.DataFrame(frame)
df_1.to_csv('VK-bert-MARCH-2023.csv', sep=',', index=False, header=False)
df_1.to_excel('VK-bert-MARCH-2023.xlsx', index=False, header=False)

In [ ]:
df_1 = pd.read_csv('VK-bert-MARCH-2023.csv')

In [ ]:
df_1

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_barchart()

In [ ]:
topic_model.visualize_distribution(probs[200], min_probability=0.015)

In [ ]:
topic_model.visualize_heatmap(n_clusters=len(freq)-1, width=1000, height=1000)  # кол-во кластеров должно быть меньше числа топиков или равно ему

In [ ]:
topic_model.visualize_term_rank()